In [3]:
import re
import pandas as pd
df = pd.read_csv("hf://datasets/regicid/lrfaf_v2/corpus.csv")


In [4]:
from tqdm import tqdm
import re

f = open("poetes_rap.txt","r")
a = f.read()
poetes_names = a.split('\n')[:-1]

mentions = {}
for p in tqdm(poetes_names):#refaire en case-sensitive
    pattern = re.compile(rf"\b{re.escape(p)}\b", flags=re.IGNORECASE)

    poet_lines = []  # list of {url, line_number, line}

    for i,text in enumerate(df.lyrics):
        url = df.url[i]
        if not isinstance(text, str):continue
        lines = text.split("\n")

        for line_no, line in enumerate(lines):
            if pattern.search(line):
                poet_lines.append({
                    "url": url,
                    "line_number": line_no,
                    "line": (
                                (lines[line_no - 1].strip() if line_no > 0 else "") + "\n" +
                                lines[line_no].strip() + "\n" +
                                (lines[line_no + 1].strip() if line_no < len(lines) - 1 else "")
                            )
                })

    mentions[p] = poet_lines


100%|█████████████████████████████████████████████████████████████████████████████████████████████| 31/31 [01:26<00:00,  2.78s/it]


In [7]:
len(mentions["Victor Hugo"])

52

In [20]:
"""
Batch inference using MLX (optimized for Apple Silicon)
Efficiently processes ~1000 prompts
"""

from mlx_lm import load, generate
from mlx_lm.sample_utils import make_sampler
sampler = make_sampler(temp=0.7, top_p=0.9)

# Load model and tokenizer
# MLX is optimized for Apple Silicon (M1/M2/M3)
model, tokenizer = load("Qwen/Qwen3-4B")

def format_prompt(user_message):
    """Format prompt using Qwen chat template"""
    messages = [
        {"role": "system", "content": "You are a helpful assistant."},
        {"role": "user", "content": user_message}
    ]
    # Apply the chat template
    return tokenizer.apply_chat_template(
        messages, 
        tokenize=False, 
        add_generation_prompt=True,
        enable_thinking=True
    )

# Example: Create 1000 prompts
prompts = []
for poet in reversed(mentions):
    for i in range(len(mentions[poet])):
        p = format_prompt(f"""I am going to give you lines of French rap, where the poet {poet} is mentioned. I want you to tell me whether the rapper compares himself to the poet (answer A) or distanciates himself from to the poet (answer B), or neither (answer C). Comparing to the poet can mean that the rapper says that he is like him, as good as him, better than him or something else. Distanciating him can be that the rapper says that he is nothing like the rapper, or that he is not interested in the poet.
            I want you to answer in json with the answer as A, B or C (defined above) and stick to the following format: {{"answer":..., "justification": ...}}
            Here are the lyrics: {mentions[poet][i]["line"]}
            """)
        prompts.append(p)

# Run inference on all prompts
outputs = []
for i, prompt in enumerate(prompts):
    if i % 50 == 0:
        print(f"Processing prompt {i+1}/{len(prompts)}...")
    # Generate response with custom sampler
    response = generate(
        model=model,
        tokenizer=tokenizer,
        prompt=prompt,
        max_tokens=1024,
        sampler=sampler,  # Use custom sampler for temp/top_p
        verbose=True,
    )
    
    outputs.append(response)

# Process results
for i, output in enumerate(outputs):
    user_msg = prompts[i].split("<|im_start|>user\n")[-1].split("<|im_end|>")[0]
    print(f"\n--- Prompt {i+1} ---")
    print(f"User: {user_msg.strip()}")
    print(f"Assistant: {output}")
    
    # Save to file if needed
    # with open(f"output_{i}.txt", "w") as f:
    #     f.write(output)

print(f"\nCompleted {len(outputs)} inferences!")


Fetching 10 files:   0%|          | 0/10 [00:00<?, ?it/s]

Processing prompt 1/713...
<think>
Okay, let's tackle this. The user provided some French rap lyrics and wants to know if the rapper is comparing himself to Cendrars (A), distancing himself (B), or neither (C). 

First, I need to look at the lines. The lyrics mention "Blaise Cendrars" directly. The line says "tu lis Faulkner et Blaise Cendrars" which translates to "you read Faulkner and Blaise Cendrars." The rapper is mentioning the poet in the same sentence as another author, Faulkner. 

Now, the key is to see if the rapper is comparing himself to Cendrars. The line "tu lis..." is in the second person, so it's talking about someone else (the listener) reading these authors. The rapper isn't directly comparing himself to Cendrars. Instead, he's pointing out that the listener is reading both Faulkner and Cendrars. 

The rapper's own situation is described as "J'n'ai que l'âge de mes vertèbres, mes espoirs sont plus anciens," which means "I have only the age of my vertebrae, my hopes are

In [33]:
mentions["Ronsard"]

[{'url': 'https://genius.com/Lucio-bukowski-le-poete-et-le-vandale-lyrics',
  'line_number': 43,
  'line': 'Entre une poitrine de sage-femme et la claque, quel bon soir\nMon premier cri fut un alexandrin de Pierre Ronsard\nL’enfance est toujours poétique, j’avais un truc en moins'},
 {'url': 'https://genius.com/Fally-ipupa-lourdes-lyrics',
  'line_number': 13,
  'line': '\nRONSARD BONGONGO (Kanza)\nYo okobenganaka moto Alex Mfumu Nsi hymne national'},
 {'url': 'https://genius.com/Le-pakkt-immortels-lyrics',
  'line_number': 58,
  'line': "Mais nos voix resteront là calés sur des sons saccadés\nComme celles de Ronsard mes fleurs à moi de vont pas faner\nEt c'est pour ça que nos fans affamés ne seront jamais rassasiés"},
 {'url': 'https://genius.com/Kheiron-mauvaises-herbes-lyrics',
  'line_number': 53,
  'line': "J’avais pas les questions, j’ai posé les réponses\nMignonne, allons voir si Ronsard a cultivé les ronces\nY a pas d'repos le dimanche, on laisse ça au Pape"},
 {'url': 'https:/

In [41]:
import pandas as pd

import ast
i = 0
jsons = []
answers = []
for o in outputs:
    try:
        j = ast.literal_eval(o.split("</think>")[-1].strip())
        jsons.append(j)
        answers.append(j.get("answer"))
    except:
        i+=1
        jsons.append(None)
        answers.append(None)

rows = []
for key, list_of_dicts in mentions.items():
    for d in list_of_dicts:
        row = d.copy()
        row["poet"] = key
        rows.append(row)

df = pd.DataFrame(rows)
df["json"] = jsons
df["answers"] = answers

In [59]:
df.loc[df.groupby("poet")["answers"].transform("size") >= 10].assign(is_A = df["answers"] == "A").groupby("poet")["is_A"].mean().sort_values()


poet
Rimbaud        0.290909
Verlaine       0.317073
Lamartine      0.500000
Neruda         0.500000
Baudelaire     0.510791
Victor Hugo    0.538462
La Fontaine    0.562914
Prévert        0.575758
Césaire        0.660377
Apollinaire    0.666667
Aragon         0.761905
Name: is_A, dtype: float64

In [60]:
df.to_csv("/Users/b.de-courson/code/poetes_rap/qwen.csv")